In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from datetime import datetime
import cufflinks as cf
cf.go_offline()
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
sns.set(rc={'figure.figsize':(16,9)} ,font_scale=1.5 , palette='viridis' , style='whitegrid' )

In [2]:
cf.getThemes()

['ggplot', 'pearl', 'solar', 'space', 'white', 'polar', 'henanigans']

In [3]:
cf.set_config_file(offline=True , sharing='public',theme='pearl')

In [4]:
my=['#55efc4','#81ecec','#74b9ff','#a29bfe','#00b894','#00cec9','#0984e3','#6c5ce7','#ff9f43','#fdcb6e',
        '#fab1a0','#e17055','#ff7675','#d63031','#fd79a8','#e84393','#c7ecee','#b2bec3','#636e72','#2d3436']

In [5]:
df= pd.read_csv('aop.csv')

## on some table am only gonna show the first 5 row cause the table is long

In [6]:
df.head()

Date        Event Details  Billing on  \
0  2018-04-17 08:29:15 UTC    Installed     NaN         NaN   
1  2018-04-17 09:38:34 UTC    Installed     NaN         NaN   
2  2018-04-17 12:39:04 UTC    Installed     NaN         NaN   
3  2018-04-17 14:49:35 UTC    Installed     NaN         NaN   
4  2018-04-17 14:58:04 UTC  Uninstalled     NaN         NaN   

                         Shop name Shop country                    Shop domain  
0  AOP Development & Testing Store           BM         aopstore.myshopify.com  
1                  alloverprintapp           US  alloverprintapp.myshopify.com  
2                        kevinsaop           GB        kevinsaop.myshopify.com  
3                           canaop           GB           canaop.myshopify.com  
4                           canaop           GB           canaop.myshopify.com

In [7]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 38747 entries, 0 to 38746
Data columns (total 7 columns):
Date            38747 non-null object
Event           38747 non-null object
Details         2418 non-null object
Billing on      0 non-null float64
Shop name       38747 non-null object
Shop country    38747 non-null object
Shop domain     38747 non-null object
dtypes: float64(1), object(6)
memory usage: 2.1+ MB


In [8]:
df['Details'].value_counts().head(10)

Does not meet my needs                  1071
Not needed anymore                       288
Other                                    224
App is not performing well               128
I found a better app                     126
Ne répond pas à mes besoins               58
App is not worth the cost                 40
Je n'en ai plus besoin                    15
Entspricht nicht meinen Bedürfnissen      15
No satisface mis necesidades              13
Name: Details, dtype: int64

In [9]:
df['Event'].value_counts()

Installed          18197
Closed Store        8886
Uninstalled         8390
Re-opened Store     3274
Name: Event, dtype: int64

# Section1
## Let's start by an event count base on store country, there was a lot so I made the second one to just show top 10 country

In [10]:
df.groupby(['Event','Shop country'])['Shop name'].count().unstack().iplot(kind='bar',colors=my)

In [11]:
df[(df['Shop country']=='US') | (df['Shop country']=='GB') | (df['Shop country']=='CA') | (df['Shop country']=='FR') | (df['Shop country']=='AU')
   | (df['Shop country']=='DE') | (df['Shop country']=='VN') | (df['Shop country']=='PH') | (df['Shop country']=='ES')
   | (df['Shop country']=='NL')].groupby(['Event','Shop country'])['Shop name'].count().unstack().iplot(kind='bar',colors=my)

In [12]:
df['Date']=pd.to_datetime(df['Date'])
df['date']=df['Date'].dt.date
df['time']=df['Date'].dt.time
df['Yearh_Month']=df['Date'].dt.to_period('M')

C:\ProgramData\Anaconda3\lib\site-packages\pandas\core\arrays\datetimes.py:1172: UserWarning:

Converting to PeriodArray/Index representation will drop timezone information.



In [13]:
i=df[df['Event']=='Installed'].groupby('Yearh_Month')['Event'].count()
i.columns=['Install']
u=df[df['Event']=='Uninstalled'].groupby('Yearh_Month')['Event'].count()
u.columns=['Uninstalled']
c=df[df['Event']=='Closed Store'].groupby('Yearh_Month')['Event'].count()
c.columns=['Closed Store']
r=df[df['Event']=='Re-opened Store'].groupby('Yearh_Month')['Event'].count()
r.columns=['Re-opened Store']

In [14]:
i=pd.DataFrame(i)
u=pd.DataFrame(u)
c=pd.DataFrame(c)
r=pd.DataFrame(r)
iucr=pd.concat([i,u,c,r],axis=1)
iucr.columns=['Installed','Uninstalled','Closed store','Re_open store']
iucr.iplot(colors=my,title='Number of each event for each month /Line chart')
iucr.iplot(kind='bar',colors=my,title='Number of each event for each month /bar chart')

------------------------------------------------------------------------------------------------------------------------------
------------------------------------------------------------------------------------------------------------------------------
------------------------------------------------------------------------------------------------------------------------------
------------------------------------------------------------------------------------------------------------------------------
------------------------------------------------------------------------------------------------------------------------------

## Section2

# now am gonna do something that might not be useful because the data is not related to the marketplace, the event is totally related to each individual problems and motivations, but...

# this is called seasonal decomposition, in short term, it decomposes time series into Trend, Seasonality, Residual,  the point of this is to focus on Residual plot to investigate what happened on a particular day if we see a drop or a spike in the plot

## ex: if we had some plain company data and we look at residual we will see a drop at April 2010 if we investigate what happened at that day we will see that there was that volcano could that cover Europe

## I look up at some date events but I can't confirm that it the actual reason why we see drops or spikes because it not the kind of data to do so, and maybe at some point in resudual there might be some event happend that only you know of, like adding new feature to the app ot facebook ads, IKD,  it's just fun to see it

In [15]:
import statsmodels.api as sm

In [16]:
ii=df[df['Event']=='Installed'].groupby('Date')['Event'].count()
inn=pd.DataFrame(dict(date=ii.index, install=ii.values))
inn=inn.set_index('date')
decomposition = sm.tsa.seasonal_decompose(inn['install'].resample('SM').sum(), freq=6)
o=pd.DataFrame(inn['install'].resample('SM').sum())
t=pd.DataFrame(decomposition.trend)
s=pd.DataFrame(decomposition.seasonal)
r=pd.DataFrame(decomposition.resid)
tsr=pd.concat([o,t,s,r],axis=1)
tsr.columns=['Observed','Trend','Seasonal','Residual']


In [17]:
un=df[df['Event']=='Uninstalled'].groupby('Date')['Event'].count()
unn=pd.DataFrame(dict(date=un.index, Uninstalled=un.values))
unn=unn.set_index('date')
udecomposition = sm.tsa.seasonal_decompose(unn['Uninstalled'].resample('SM').sum(), freq=6)
uo=pd.DataFrame(unn['Uninstalled'].resample('SM').sum())
ut=pd.DataFrame(udecomposition.trend)
us=pd.DataFrame(udecomposition.seasonal)
ur=pd.DataFrame(udecomposition.resid)
utsr=pd.concat([uo,ut,us,ur],axis=1)
utsr.columns=['Observed','Trend','Seasonal','Residual']

In [18]:
tsr.iplot(subplots=True,shape=(4,1),shared_xaxes=True,vertical_spacing=.02,title='Installed time series decomposition',colors=my)
utsr.iplot(subplots=True,shape=(4,1),shared_xaxes=True,vertical_spacing=.02,title='Uninstalled time series decomposition',colors=my)

------------------------------------------------------------------------------------------------------------------------------
------------------------------------------------------------------------------------------------------------------------------
------------------------------------------------------------------------------------------------------------------------------
------------------------------------------------------------------------------------------------------------------------------
------------------------------------------------------------------------------------------------------------------------------

# Section3

# now let's see how many time an event accrue for each Store

In [19]:
gf=pd.get_dummies(df.Event)
gf['Shop name']=df['Shop name']
gf['Date']=df['Date']

# I sort the first table by installed count and only showed the top 10, ofc I can't make it as an excel file and send it to you if you want

In [20]:
gf.groupby('Shop name').sum().sort_values('Installed',ascending=False,).head(10)

Closed Store  Installed  Re-opened Store  \
Shop name                                                                
The Fashion Store™️                      0          9                0   
By Dusign                                2          8                2   
Haustiere sind meine Passion             0          8                0   
Wolvestuff                               1          7                1   
vmv-Denmark                              0          7                0   
Sassy Bassett Designs                    2          6                2   
Funerals For The Flesh                   0          6                0   
TrendHackr                               0          6                0   
vmv-spain2                               0          6                0   
Urbanvandal clothing                     0          6                0   

                              Uninstalled  
Shop name                                  
The Fashion Store™️                     9  
By Dusign                               8  
Haustiere sind meine Passion            8  
Wolvestuff                              6  
vmv-Denmark                             6  
Sassy Bassett Designs                   6  
Funerals For The Flesh                  6  
TrendHackr                              5  
vmv-spain2                              5  
Urbanvandal clothing                    6

# In this table i sort it by Re-opened Event, just for fun, and ohh boy, HUNTLES with the 17 Re-opned, that guy need some help from you.

In [21]:
gf.groupby('Shop name').sum().sort_values('Re-opened Store',ascending=False,).head(10)

Closed Store  Installed  Re-opened Store  Uninstalled
Shop name                                                                   
HUNTEES                          17          1               17            0
Fly By Nature                    11          1               11            0
LifeSideAssistance               10          1               10            0
Infinity Decals                   9          1                9            0
ShopOverNet.com                  10          1                9            0
YourTrumpShop.com                 9          2                9            1
Byrd's Paradise & Co.             9          1                8            0
Charged Independence              7          0                7            0
ilovesierraleone                  7          1                7            0
BlackKoko                         7          1                7            0

# A brief graph shows how many times an event occurrence on every store, you can click on the right graph key where there is the name of event and click on them to toggle if you want to see each one alone.

## So if you hover over zeros you will see a remarkable thing 10.23K did not Uninstall the app at all (but their store might have been closed, I made you a deep analysis below).

## And you have 939 Store that does not install the app, hum that weird, if they didn't install the app how so they get here, must be a bug ??!


In [22]:
gf.groupby('Shop name').sum().iplot("histogram",colors=my,title='event occurrence',xTitle='event occurrence count',yTitle='number of store')

------------------------------------------------------------------------------------------------------------------------------
------------------------------------------------------------------------------------------------------------------------------
------------------------------------------------------------------------------------------------------------------------------
------------------------------------------------------------------------------------------------------------------------------
------------------------------------------------------------------------------------------------------------------------------


# Section4

# your VIP Groups

## In the graph, you can click on the event name on the right to toggle  them so that the graph is easier to read.

In [23]:
v=gf.groupby('Shop name').sum()
a=v[(v['Installed'] == v['Uninstalled']) & (v['Closed Store']==0) ]
b=v[(v['Installed'] > v['Uninstalled']) & (v['Closed Store']==0) ]
c=v[(v['Re-opened Store'] == v['Closed Store'])  &
  (v['Installed'] > v['Uninstalled'])].sort_values('Installed',ascending=False,)
d=v[(v['Closed Store']==0) & (v['Uninstalled'] == 0 )].sort_values('Installed',ascending=False,)

# I decide to separate them based on conditions, and I end up with 4 groups.

**Groupe A**: those just install the app to test it some of them install and uninstall the app more than 9 times,maybe they have some doubt.

**Groupe B**: Those know what there doing, the store never got close, but still some of them uninstall and install the app again, mabybe they need some care, especialy those who uninstall the app more than once, but the arent much out of 4116 only 217 store who unintall it at leaste once, but they reinstall it after that, the elite are groupe D.

**Groupe C**: They didn't uninstall the ap from there store but they some of them got there store close, They are somewhat loyal but maybe they need some help in the long run, maybe a discount ... IDK.

**Groupe D**: Elite, not financially, but you win there loyalty, those never uninstall the app and there store never got close, are they doing okay? IDK x).

In [24]:
a.iplot(kind='histogram',colors=my,
title='Groupe A: 6119 Stores Who Install and Uninstall the app without having their store getting Closed.',
xTitle='Event count',yTitle='Store Count',)
b.iplot(kind='histogram',colors=my,
title='Groupe B: 4116 Stores still have the App installed and there store never got Closed.',
xTitle='Event count',yTitle='Store Count',)
c.iplot(kind='histogram',colors=my,
title='Groupe C: 5065 Stores got there store closed but they reopen it and they still have the app on there store ',
xTitle='Event count',yTitle='Store Count',)
d.iplot(kind='histogram',colors=my,
title='Groupe D: 3869 Stores didnt get close and they did not uninstall the app, not even once.',
xTitle='Event count',yTitle='Store Count',)


------------------------------------------------------------------------------------------------------------------------------
------------------------------------------------------------------------------------------------------------------------------
------------------------------------------------------------------------------------------------------------------------------
------------------------------------------------------------------------------------------------------------------------------
------------------------------------------------------------------------------------------------------------------------------

# Setcion 5

# Now to the hardest part how long does it take people to uninstall the app after the first install.

In [25]:
df2=pd.read_csv('aop.csv')
gf2=pd.get_dummies(df2.Event)
gf2['Shop name']=df2['Shop name']
gf2['Date']=df2['Date']
gf2.loc[gf2['Installed']==1,'Installed']=gf2.Date
gf2.loc[gf2['Uninstalled']==1,'Uninstalled']=gf2.Date
gf2.loc[gf2['Closed Store']==1,'Closed Store']=gf2.Date
gf2.loc[gf2['Re-opened Store']==1,'Re-opened Store']=gf2.Date
gf2.loc[gf2['Installed']==0,'Installed']=','
gf2.loc[gf2['Uninstalled']==0,'Uninstalled']=','
gf2.loc[gf2['Closed Store']==0,'Closed Store']=','
gf2.loc[gf2['Re-opened Store']==0,'Re-opened Store']=','
gf2['Installed']=gf2['Installed']+str(';')
gf2['Uninstalled']=gf2['Uninstalled']+str(';')
gf2['Closed Store']=gf2['Closed Store']+str(';')
gf2['Re-opened Store']=gf2['Re-opened Store']+str(';')
gf2=gf2.groupby('Shop name')['Installed','Uninstalled','Closed Store','Re-opened Store'].sum()
gf2['Installed']=gf2['Installed'].apply(lambda x : x.split(';')[0])
gf2['Uninstalled']=gf2['Uninstalled'].apply(lambda x : x.split(';')[-2])
gf2['Closed Store']=gf2['Closed Store'].apply(lambda x : x.split(';')[-2])
gf2['Re-opened Store']=gf2['Re-opened Store'].apply(lambda x : x.split(';')[-2])
gf2.loc[gf2['Installed']==',','Installed']=np.nan
gf2.loc[gf2['Uninstalled']==',','Uninstalled']=np.nan
gf2.loc[gf2['Closed Store']==',','Closed Store']=np.nan
gf2.loc[gf2['Re-opened Store']==',','Re-opened Store']=np.nan
gf2['Installed']=pd.to_datetime(gf2['Installed'])
gf2['Uninstalled']=pd.to_datetime(gf2['Uninstalled'])
gf2['Closed Store']=pd.to_datetime(gf2['Closed Store'])
gf2['Re-opened Store']=pd.to_datetime(gf2['Re-opened Store'])
gf2['Difference I_U D']=(gf2['Uninstalled']-gf2['Installed']).astype('timedelta64[D]')
gf2['Installed month']=gf2['Installed'].dt.month
gf2['Installed day']=gf2['Installed'].dt.day
gf2['Installed hour']=gf2['Installed'].dt.hour
gf2['Installed dayofweek']=gf2['Installed'].dt.dayofweek
gf2['Uninstalled month']=gf2['Uninstalled'].dt.month
gf2['Uninstalled day']=gf2['Uninstalled'].dt.day
gf2['Uninstalled hour']=gf2['Uninstalled'].dt.hour
gf2['Uninstalled dayofweek']=gf2['Uninstalled'].dt.dayofweek

## So just a disclamer.

**-Difference I_U D** represents the difference of date between the first install and last uninstall, and it in day unite, so if you see **NaN**, it means that the app is still installed on the store, and if you see a **0**, it means the app got installed and uninstalled in less than a day, else any number represents a day
**ex** #BarkForMentalHealth uninstalled the app after 39 day

**Installed month-day-hour** are self-explanatory

**Installed dayofweek** The day of the week with Monday=0, Sunday=6. , I could go with the **Installed day**, but the day of the week has more value because Sunday is Sunday doesn't matter if it the 5th or 24th of the month that much, **Installed day** but it matters when I want to determine the behaviors in first days of month and lest days of month.

In [26]:
gf2.head()

Installed               Uninstalled  \
Shop name                                                                  
ShinyTee            2018-10-23 20:34:25+00:00                       NaT   
"Driplot"            2018-11-12 07:53:37+00:00                       NaT   
"Why Not" Gifts      2018-09-07 00:36:52+00:00                       NaT   
#BarkForMentalHealth 2019-07-23 19:45:45+00:00 2019-08-31 20:43:57+00:00   
#Esprit-Pêcheur      2018-07-08 19:42:11+00:00                       NaT   

                                  Closed Store Re-opened Store  \
Shop name                                                        
ShinyTee            2018-10-24 12:28:00+00:00             NaT   
"Driplot"            2018-11-18 08:49:10+00:00             NaT   
"Why Not" Gifts                            NaT             NaT   
#BarkForMentalHealth                       NaT             NaT   
#Esprit-Pêcheur      2019-04-25 13:25:52+00:00             NaT   

                      Difference I_U D  Installed month  Installed day  \
Shop name                                                                
ShinyTee                          NaN             10.0           23.0   
"Driplot"                          NaN             11.0           12.0   
"Why Not" Gifts                    NaN              9.0            7.0   
#BarkForMentalHealth              39.0              7.0           23.0   
#Esprit-Pêcheur                    NaN              7.0            8.0   

                      Installed hour  Installed dayofweek  Uninstalled month  \
Shop name                                                                      
ShinyTee                       20.0                  1.0                NaN   
"Driplot"                        7.0                  0.0                NaN   
"Why Not" Gifts                  0.0                  4.0                NaN   
#BarkForMentalHealth            19.0                  1.0                8.0   
#Esprit-Pêcheur                 19.0                  6.0                NaN   

                      Uninstalled day  Uninstalled hour  Uninstalled dayofweek  
Shop name                                                                       
ShinyTee                         NaN               NaN                    NaN  
"Driplot"                         NaN               NaN                    NaN  
"Why Not" Gifts                   NaN               NaN                    NaN  
#BarkForMentalHealth             31.0              20.0                    5.0  
#Esprit-Pêcheur                   NaN               NaN                    NaN

In [27]:
gf2['Difference I_U D'].dropna().iplot(kind='histogram',colors=my,title='The difference of Days between Install-Uninstall Event',
                                       xTitle='Number of days',yTitle='Count')

In [28]:
print('seems like a lot of people uninstall the app in less than a day here is a little table shows exact values.')
print('ex: 3306 Uninstall the app in less than a day')
gf2['Difference I_U D'].dropna().value_counts().head()

seems like a lot of people uninstall the app in less than a day here is a little table shows exact values.
ex: 3306 Uninstall the app in less than a day


0.0    3306
1.0     240
2.0     167
3.0     149
5.0     107
Name: Difference I_U D, dtype: int64

In [29]:
print('Here is an interesting list, those stores uninstall the app after a long journey')
print("Most of them work with the app for over a year, and their Stores didn't get closed for sure, do you need to contact them about some new feature, maybe, IDK")
gf2['Difference I_U D'].sort_values(ascending=False).head(25)

Here is an interesting list, those stores uninstall the app after a long journey
Most of them work with the app for over a year, and their Stores didn't get closed for sure, do you need to contact them about some new feature, maybe, IDK


Shop name
Beyond Bionda            450.0
Finleys                  425.0
PAPAWGEAR                421.0
54th Boulevard           420.0
Homebody Friends         420.0
ZizZak                   417.0
Great Things 4 Family    413.0
gaatshirts.com           412.0
Helicity Designs         409.0
Trendanchor.de           407.0
Melaninful               404.0
BellaBargains            404.0
The Street's Finest      402.0
Trifecta Racing          399.0
haidaclothing            398.0
The Owl Bootique         398.0
Bougie Girls Shop        397.0
Atikapu                  383.0
Art Fever                378.0
Amandla Apparel          365.0
Simone Studios           362.0
SuperLdN                 359.0
808strongco              357.0
Ararose Clothing         355.0
TD Gift Solutions.com    354.0
Name: Difference I_U D, dtype: float64

In [30]:
print('same as above but it for store who started in 2019 and uninstall the app')
(gf2[gf2['Installed']>"2019-01-01"]['Uninstalled']-gf2[gf2['Installed']>"2019-01-01"]['Installed']).astype('timedelta64[D]').dropna().sort_values(ascending=False).head(25)

same as above but it for store who started in 2019 and uninstall the app


Shop name
AZHATS                           243.0
Bandzclub                        233.0
Magic 3D Tee | All Over Print    233.0
Chesapeake Collection            229.0
BOXELS                           227.0
Collection 53                    227.0
Ski-Tees and Apparel             226.0
Shalisha Closet                  216.0
Neverland Clothing               214.0
Dad Bod Tees                     210.0
Royal Realm Stylz                207.0
KRAKUSSEN                        203.0
Vigarustore                      203.0
Gosh Doggit                      199.0
JABRIL                           197.0
Stoopid Froot                    197.0
BroTank.com                      196.0
Paul Aramouni                    190.0
Everybody's cool                 189.0
VIICES                           188.0
Clean Apparel                    188.0
BillyHead                        187.0
Restrained Grace                 187.0
Pezlondon                        187.0
Keep Active & Hustle             180.0
dtype: float64

------------------------------------------------------------------------------------------------------------------------------
------------------------------------------------------------------------------------------------------------------------------
------------------------------------------------------------------------------------------------------------------------------
------------------------------------------------------------------------------------------------------------------------------
------------------------------------------------------------------------------------------------------------------------------

# Setcion 6

## Moving out from the difference between the installed app and uninstall app date, now we will analyze the installed and uninstall date and maybe spot some behaviors.

## Should we take action base on this graph, yes and no, for install/uninstall day, hour, day of week yes, but I don't believe that we can drive to a conclusion watching the month data, because the first date in the data start from April, and we are at September.

## My point is there are some months that only shows in the year of 2018(October - November - December), some only in 2019(January, February, Mars), and some of them repeated in 2018 and 2019 so that a bit unfair, but tho June is repeated in 2018 and 2019 yet still it has a low install/uninstall rate.

In [31]:
gf2[['Installed month','Installed day','Installed hour','Installed dayofweek']].iplot(kind='histogram',subplots=True,shape=(4,1),title='Installed count',colors=my)
gf2[['Uninstalled month','Uninstalled day','Uninstalled hour','Uninstalled dayofweek']].iplot(kind='histogram',subplots=True,shape=(4,1),title='Uninstalled count',colors=my)

## Matrix, Cross table, the idea of this is to see how each value interact with others, for example, you can see that there are fewer people installing the app during 5-11AM

## days with higher install rate are Monday, Tuesday, Wednesday with some outliers in Tuesday, some of them install the app at 1-2 AM but it UTC and we have around 130+ country, so maybe I can focus on the US with having a huge amounts of shops next time

In [32]:
gf2.groupby(['Installed dayofweek','Installed hour'])['Installed'].count().unstack().iplot(kind='heatmap',colorscale='-ylgnbu',
title='Installed app date matrix Day of the week - Hour',xTitle='Day of week',yTitle='Hour',zTitle='Count',)
gf2.groupby(['Installed dayofweek','Installed month'])['Installed'].count().unstack().iplot(kind='heatmap',colorscale='-ylgnbu',
title='Installed app date matrix Day of the week - Month',xTitle='Day of week',yTitle='Month',zTitle='Count',)

## same concept for uninstalling 

In [33]:
gf2.groupby(['Uninstalled dayofweek','Uninstalled hour'])['Uninstalled'].count().unstack().iplot(kind='heatmap',colorscale='-ylgnbu',
title='Uninstalled app date matrix Day of the week - Hour',xTitle='Day of week',yTitle='Hour',zTitle='Count',)
gf2.groupby(['Uninstalled dayofweek','Uninstalled month'])['Uninstalled'].count().unstack().iplot(kind='heatmap',colorscale='-ylgnbu',
title='Uninstalled app date matrix Day of the week - Month',xTitle='Day of week',yTitle='Month',zTitle='Count',)

------------------------------------------------------------------------------------------------------------------------------
------------------------------------------------------------------------------------------------------------------------------
------------------------------------------------------------------------------------------------------------------------------
------------------------------------------------------------------------------------------------------------------------------
------------------------------------------------------------------------------------------------------------------------------

# Setcion 6

# Matrix for USA but in UTC time, so you can see when the support need to be active the most

In [34]:
df2=pd.read_csv('aop.csv')
gf2=pd.get_dummies(df2[df2['Shop country']=="US"].Event)
gf2['Shop name']=df2[df2['Shop country']=="US"]['Shop name']
gf2['Date']=df2[df2['Shop country']=="US"]['Date']
gf2.loc[gf2['Installed']==1,'Installed']=gf2.Date
gf2.loc[gf2['Uninstalled']==1,'Uninstalled']=gf2.Date
gf2.loc[gf2['Closed Store']==1,'Closed Store']=gf2.Date
gf2.loc[gf2['Re-opened Store']==1,'Re-opened Store']=gf2.Date
gf2.loc[gf2['Installed']==0,'Installed']=','
gf2.loc[gf2['Uninstalled']==0,'Uninstalled']=','
gf2.loc[gf2['Closed Store']==0,'Closed Store']=','
gf2.loc[gf2['Re-opened Store']==0,'Re-opened Store']=','
gf2['Installed']=gf2['Installed']+str(';')
gf2['Uninstalled']=gf2['Uninstalled']+str(';')
gf2['Closed Store']=gf2['Closed Store']+str(';')
gf2['Re-opened Store']=gf2['Re-opened Store']+str(';')
gf2=gf2.groupby('Shop name')['Installed','Uninstalled','Closed Store','Re-opened Store'].sum()
gf2['Installed']=gf2['Installed'].apply(lambda x : x.split(';')[0])
gf2['Uninstalled']=gf2['Uninstalled'].apply(lambda x : x.split(';')[-2])
gf2['Closed Store']=gf2['Closed Store'].apply(lambda x : x.split(';')[-2])
gf2['Re-opened Store']=gf2['Re-opened Store'].apply(lambda x : x.split(';')[-2])
gf2.loc[gf2['Installed']==',','Installed']=np.nan
gf2.loc[gf2['Uninstalled']==',','Uninstalled']=np.nan
gf2.loc[gf2['Closed Store']==',','Closed Store']=np.nan
gf2.loc[gf2['Re-opened Store']==',','Re-opened Store']=np.nan
gf2['Installed']=pd.to_datetime(gf2['Installed'])
gf2['Uninstalled']=pd.to_datetime(gf2['Uninstalled'])
gf2['Closed Store']=pd.to_datetime(gf2['Closed Store'])
gf2['Re-opened Store']=pd.to_datetime(gf2['Re-opened Store'])
gf2['Difference I_U D']=(gf2['Uninstalled']-gf2['Installed']).astype('timedelta64[D]')
gf2['Installed month']=gf2['Installed'].dt.month
gf2['Installed day']=gf2['Installed'].dt.day
gf2['Installed hour']=gf2['Installed'].dt.hour
gf2['Installed dayofweek']=gf2['Installed'].dt.dayofweek
gf2['Uninstalled month']=gf2['Uninstalled'].dt.month
gf2['Uninstalled day']=gf2['Uninstalled'].dt.day
gf2['Uninstalled hour']=gf2['Uninstalled'].dt.hour
gf2['Uninstalled dayofweek']=gf2['Uninstalled'].dt.dayofweek

In [35]:
gf2[['Installed month','Installed day','Installed hour','Installed dayofweek']].iplot(kind='histogram',subplots=True,shape=(4,1),title='Installed count',colors=my)
gf2[['Uninstalled month','Uninstalled day','Uninstalled hour','Uninstalled dayofweek']].iplot(kind='histogram',subplots=True,shape=(4,1),title='Uninstalled count',colors=my)

In [36]:
gf2.groupby(['Installed dayofweek','Installed hour'])['Installed'].count().unstack().iplot(kind='heatmap',colorscale='-ylgnbu',
title='Installed app date matrix Day of the week - Hour',xTitle='Day of week',yTitle='Hour',zTitle='Count',)
gf2.groupby(['Installed dayofweek','Installed month'])['Installed'].count().unstack().iplot(kind='heatmap',colorscale='-ylgnbu',
title='Installed app date matrix Day of the week - Month',xTitle='Day of week',yTitle='Month',zTitle='Count',)


In [37]:
gf2.groupby(['Uninstalled dayofweek','Uninstalled hour'])['Uninstalled'].count().unstack().iplot(kind='heatmap',colorscale='-ylgnbu',
title='Uninstalled app date matrix Day of the week - Hour',xTitle='Day of week',yTitle='Hour',zTitle='Count',)
gf2.groupby(['Uninstalled dayofweek','Uninstalled month'])['Uninstalled'].count().unstack().iplot(kind='heatmap',colorscale='-ylgnbu',
title='Uninstalled app date matrix Day of the week - Month',xTitle='Day of week',yTitle='Month',zTitle='Count',)